In [2]:
import requests
from dotenv import load_dotenv
import os
import re

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me to find that the text is relevant to the question or not.
You are given a question and a text.
You must evaluate the text based on the question and return "1" if the text is relevant to the question and "0" if the text is not relevant to the question.
 
be carefull, I have chosen the text randomly from my dataset so the text must answer the question independently.
You must return the result in the following format:
{{"result": "1" or "0"}}
"""

question = "چرا خورشید اینقدر داغ است؟"
texts = [
            "سیاراتی که در مدار نزدیک به ستاره های کوتوله سرخ قرار دارند، به دلیل نزدیکی به ستاره مادر، تحت تابش تشعشعات شدید قرار می گیرند. این تابش می تواند شرایط زیست محیطی را به شدت تحت تأثیر قرار دهد و ممکن است تنها مکان هایی که حیات در آنجا امکان وجود دارد، زیر لایه های ضخیم یخ باشد. این شرایط می تواند مانع از شکل گیری و تکامل حیات در سطح سیاره شود.",
            "کتاب تابستان به دلیل داستان جذاب و توصیف‌های زیبا از طبیعت و زندگی، توجه تمام علاقه‌مندان به ادبیات داستانی را به خود جلب می‌کند. این کتاب نه تنها احساسات عمیق انسانی را به تصویر می‌کشد بلکه خواننده را به دنیای خاطرات شیرین تابستان‌های کودکی می‌برد.",
            "حضرت ادریس علیه السلام به عنوان منشاء و معلم بسیاری از علوم شناخته می‌شود. او به عنوان یکی از قدیمی‌ترین پیشوایان علم، افکار بشر را به سمت استدلال و دقت در بحث سوق داده است. همچنین، او اولین کسی است که علم نجوم را به الهام الهی استخراج کرده و زمین را به چهار ربع تقسیم نموده است. در دعای روز اول ماه رجب نیز به علم ادریس اشاره شده است.",
            "ستاره‌های کوتوله سرخ معمولاً به صورت دوره‌ای شعله‌هایی از پرتوهای ماورا بنفش و اشعه X ساطع می‌کنند که می‌تواند اتمسفر سیارات اطراف را از بین ببرد و احتمال تشکیل حیات را کاهش دهد. اما ستاره Ross 128 به عنوان یک ستاره آرام شناخته می‌شود و این ویژگی باعث می‌شود که شرایط بهتری برای تشکیل حیات در سیاره Ross 128b فراهم شود.",
            "پوست کودکان به دلیل عدم تکامل کامل ملانوسیت‌ها، سیستم عروقی پوستی و توانایی تولید عرق حساس است. ملانوسیت‌ها که مسئول تولید ملانین هستند، از پوست در برابر اشعه ماورای بنفش محافظت می‌کنند. همچنین، سیستم عروقی پوستی در کودکان هنوز به طور کامل توسعه نیافته و این امر می‌تواند منجر به آسیب‌پذیری بیشتر پوست شود. علاوه بر این، پوست کودکان نمی‌تواند به اندازه کافی عرق تولید کند، که باعث می‌شود رطوبت پوست کاهش یابد. به همین دلیل، پوست کودکان به ویژه نوزادان به نسبت وزن بدن در معرض آسیب بیشتری قرار دارد.",
            "نزول این آیه به واکنش‌های معاصرین پیامبر اسلام، به ویژه ابوجهل و دیگر مخالفان، اشاره دارد که به دلیل عدم درک صحیح از معانی عمیق آیات و قدرت خداوند، به تمسخر و انکار آن می‌پرداختند. این آیه به نوعی به آنها پاسخ می‌دهد و نشان می‌دهد که حتی در آتش، درختی وجود دارد که فراتر از تصور آنهاست. این واکنش‌ها نشان‌دهنده چالش‌های اعتقادی و فکری در آن زمان بود.",
            "شرایط محیطی می‌تواند به عنوان فیلتر عمل کند زیرا عوامل متعددی مانند مقدار و نوع کالری، دما، اتمسفر، آب، خشکی، آفتاب، و بلایای طبیعی مانند آتشفشان و زلزله بر روی موجودات زنده تأثیر می‌گذارد. این عوامل می‌توانند موجودات را به چالش بکشند و تنها آن‌هایی که توانایی سازگاری با این شرایط را دارند، زنده می‌مانند و به نسل‌های بعدی منتقل می‌شوند.",
            "خشکی پوست ممکن است موقتی یا فصلی باشد. به عنوان مثال، در فصل زمستان به دلیل هوای سرد و خشک، بسیاری از افراد دچار خشکی پوست می‌شوند. در مقابل، در فصل‌های گرم و مرطوب، ممکن است این مشکل کاهش یابد. با این حال، برخی افراد ممکن است به طور دائمی با خشکی پوست مواجه باشند که نیاز به مراقبت و درمان مداوم دارد.",
            "سحابی خرچنگ دریایی، که با نام NGC 6357 شناخته می‌شود، به دلیل وجود ستاره‌های غیرمعمول روشن و عظیم در آن، به عنوان یک مکان مهم در کهکشان معرفی می‌شود. این سحابی همچنین خوشۀ ستاره‌ای باز Pismis 24 را در نزدیکی مرکز خود دارد که نشان‌دهنده فعالیت‌های شدید ستاره‌زایی در این ناحیه است. درخشش آبی در نزدیکی منطقه تشکیل ستاره داخلی ناشی از انتشار گاز هیدروژن یونیزه است که به جذابیت این سحابی افزوده است.",
            "سحابی خرچنگ ده سال نوری وسعت دارد و در مرکز آن یک تپ اختر قرار دارد. این تپ اختر به سنگینی خورشید اما به اندازه یک شهر کوچک است و ثانیه‌ای سی بار به دور خود می‌چرخد. همچنین، سحابی خرچنگ با سرعتی حدود 10000 کیلومتر بر ثانیه منبسط می‌شود و انتظار می‌رود که در چند هزار سال آینده به تدریج کم‌فروغ‌تر شده و سرانجام ناپدید گردد.",
            "وجود یک اقیانوس زیر سطحی در قمر اروپا می تواند شرایط لازم برای زندگی موجودات میکروسکوپی را فراهم کند. این اقیانوس می تواند شامل مواد مغذی و حرارت لازم برای حیات باشد. با توجه به اینکه بخار آب فوران شده از سطح اروپا ممکن است به این اقیانوس مرتبط باشد، بررسی های آینده می تواند به دانشمندان کمک کند تا پتانسیل اروپا برای تبدیل شدن به یک محل قابل سکونت را بدون نیاز به حفاری لایه یخ بررسی کنند.",
            "چگالش بوز-اینشتین حالتی از ماده است که در دماهای بسیار پایین ایجاد می‌شود و در آن اتم‌ها رفتار موجی خود را نشان می‌دهند. در این حالت، قوانین فیزیک کلاسیک به کنار می‌روند و فیزیک کوانتومی حاکم می‌شود. اتم‌ها در این حالت به گونه‌ای حرکت می‌کنند که انگار بر روی یکدیگر سوار هستند و این رفتار تنها در دماهای بسیار پایین قابل مشاهده است.",
            "در سال 2012، انجمن سلطنتی شیمی مسابقه‌ای را برای یافتن بهترین توضیح برای اثر امپمبا برگزار کرد. برنده این مسابقه نظریه‌ای را ارائه داد که علت این پدیده را 'ابرسرد شدن' می‌دانست. این نشان می‌دهد که این موضوع همچنان مورد توجه محققان و دانشمندان است و تلاش‌ها برای درک بهتر آن ادامه دارد.",
            "داستان کتاب عاشق آتشفشان در قرن هجدهم و در میان آشفتگی‌های دربار ناپلی اتفاق می‌افتد. این رمان به بررسی موضوعاتی چون عشق، تاریخ و روابط اجتماعی می‌پردازد و داستان زندگی سر ویلیام همیلتون و همسرش اِما را روایت می‌کند. همچنین، این داستان به تحولات سیاسی و اجتماعی آن زمان نیز اشاره دارد.",
            "انفجارهای هوایی به دلیل قدرت تخریب بالای خود و نادر بودن برخورد سیارک‌ها، خطرناک‌تر محسوب می‌شوند. در حالی که برخورد سیارک‌های بزرگ به ندرت اتفاق می‌افتد، انفجارهای هوایی می‌توانند به طور ناگهانی و بدون هشدار پیشین رخ دهند. به عنوان مثال، انفجار سیارکی به اندازه یک خانه در سال ۱۳۹۲ در چلیابینسک روسیه منجر به آسیب دیدن بیش از ۱۶۰۰ نفر شد. این نشان می‌دهد که انفجارهای هوایی می‌توانند تأثیرات جدی بر روی جمعیت‌های انسانی داشته باشند.",
            "پرتقال به دلیل خواص ضدعفونی‌کننده و ضد میکروبی که دارد، می‌تواند به درمان مشکلات پوستی کمک کند. به عنوان مثال، شما می‌توانید از پوست پرتقال له شده به عنوان مرهم برای اگزما و ناراحتی‌های پوستی استفاده کنید. این خاصیت به دلیل وجود ترکیبات طبیعی در پوست پرتقال است که به تسکین و بهبود وضعیت پوست کمک می‌کند.",
            "نوسانات درخشندگی ستاره KIC 8462852 به‌طور نامنظم و شدید اتفاق می‌افتند و این الگو با آنچه معمولاً در ستاره‌های دارای سیارات فراخورشیدی مشاهده می‌شود، متفاوت است. در حالی که وجود یک سیاره می‌تواند باعث نوسانات درخشندگی شود، در این مورد، نوسانات به‌قدری پیچیده و غیرقابل پیش‌بینی هستند که فرضیه‌های دیگر مانند وجود ابرهای میان ستاره‌ای، دنباله‌دارها یا حتی اَبَرسازه‌های بیگانگان فضایی نیز مطرح شده‌اند.",
            "پاریس به عنوان یک مقصد گردشگری محبوب به دلیل جاذبه‌های تاریخی، فرهنگی و هنری خود شناخته می‌شود. این شهر با برج ایفل، موزه لوور، کاتدرال نوتردام و خیابان‌های زیبا و پر از زندگی، هر ساله میلیون‌ها گردشگر را به خود جذب می‌کند. همچنین، فرهنگ غنی، غذاهای لذیذ و فضاهای رمانتیک پاریس، تجربه‌ای منحصر به فرد را برای بازدیدکنندگان فراهم می‌آورد. به همین دلیل، پاریس به عنوان 'شهر نور' و 'شهر عشق' در قلب بسیاری از مردم جهان جای دارد."
        ]
        
for text in texts:
    input_message = f"""{{"question": "{question}", "text": "{text}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100
    }

    req = requests.post(url, headers=headers, json=payload)
    print(text)
    print(req.json()['choices'][0]['message']['content'])
    print("--------------------------------")

سیاراتی که در مدار نزدیک به ستاره های کوتوله سرخ قرار دارند، به دلیل نزدیکی به ستاره مادر، تحت تابش تشعشعات شدید قرار می گیرند. این تابش می تواند شرایط زیست محیطی را به شدت تحت تأثیر قرار دهد و ممکن است تنها مکان هایی که حیات در آنجا امکان وجود دارد، زیر لایه های ضخیم یخ باشد. این شرایط می تواند مانع از شکل گیری و تکامل حیات در سطح سیاره شود.
{"result": "0"}
--------------------------------
کتاب تابستان به دلیل داستان جذاب و توصیف‌های زیبا از طبیعت و زندگی، توجه تمام علاقه‌مندان به ادبیات داستانی را به خود جلب می‌کند. این کتاب نه تنها احساسات عمیق انسانی را به تصویر می‌کشد بلکه خواننده را به دنیای خاطرات شیرین تابستان‌های کودکی می‌برد.
{{"result": "0"}}

--------------------------------
حضرت ادریس علیه السلام به عنوان منشاء و معلم بسیاری از علوم شناخته می‌شود. او به عنوان یکی از قدیمی‌ترین پیشوایان علم، افکار بشر را به سمت استدلال و دقت در بحث سوق داده است. همچنین، او اولین کسی است که علم نجوم را به الهام الهی استخراج کرده و زمین را به چهار ربع تقسیم نموده است. در دعای روز اول ماه رجب 

In [ ]:
from datasets import load_dataset

ds = load_dataset("virattt/financial-qa-10K", split="train")


In [2]:
import json
import random

with open("/home/firouzi/embedding_model/data/v2/msmarco.json", "r", encoding="utf-8") as f:
    all_dataset = json.load(f)

test_ratio = 0.001  # 10% test data

# Shuffle and split
random.shuffle(all_dataset)
split_index = int(len(all_dataset) * (1 - test_ratio))
train_data = all_dataset[:split_index]
test_data = all_dataset[split_index:]


with open("/home/firouzi/embedding_model/data/v2/msmarco_test.json", "w", encoding="utf-8") as f:
    json.dump(test_data, f, ensure_ascii=False, indent=4)

# with open("/home/firouzi/embedding_model/data/v2/train_train.json", "w", encoding="utf-8") as f:
#     json.dump(train_data, f, ensure_ascii=False, indent=4)

In [16]:
import json
from datasets import load_dataset
from tqdm import tqdm


name = "MCINext/FEVER_FA_test_top_250_only_w_correct-v2"
print(f"loading {name}")
dataset_qrel = load_dataset(name)["test"]
dataset_corpus_list = load_dataset(name,data_files="corpus/corpus.jsonl")["train"]
dataset_corpus = {}
for data in dataset_corpus_list:
    dataset_corpus[data["_id"]] = data["text"]

dataset_queries_list = load_dataset(name,data_files="queries/queries.jsonl")["train"]
dataset_queries = {}
for data in dataset_queries_list:
    dataset_queries[data["_id"]] = data["text"]


dataset = []
print("start creating dataset")
for data in dataset_qrel:

    if int(data["query-id"]) in dataset_queries and data["corpus-id"] in dataset_corpus:
        dataset.append({
            "question": dataset_queries[int(data["query-id"])],
            "passage_positive": [dataset_corpus[data["corpus-id"]]],
            "passage_negative": [],
            "passage_negative_random": [],
        })

print(f"length of dataset: {len(dataset)}")
with open(f"../data/mci/{name.split('/')[-1]}_v2.json", "w") as f:
    json.dump(dataset, f, indent=4, ensure_ascii=False)

loading MCINext/FEVER_FA_test_top_250_only_w_correct-v2
start creating dataset
length of dataset: 1171


In [ ]:
import requests
from dotenv import load_dotenv
import os
import re

load_dotenv()

qwen = False
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me to find that the text is relevant to the question or not.
You are given a question and a text.
You must evaluate the text based on the question and return "1" if the text is relevant to the question and "0" if the text is not relevant to the question.
 
be carefull, I have chosen the text randomly from my dataset so the text must answer the question independently.
You must return the result in the following format:
{{"result": "1" or "0"}}
"""

question = "چرا خورشید اینقدر داغ است؟"
texts = [
            "سیاراتی که در مدار نزدیک به ستاره های کوتوله سرخ قرار دارند، به دلیل نزدیکی به ستاره مادر، تحت تابش تشعشعات شدید قرار می گیرند. این تابش می تواند شرایط زیست محیطی را به شدت تحت تأثیر قرار دهد و ممکن است تنها مکان هایی که حیات در آنجا امکان وجود دارد، زیر لایه های ضخیم یخ باشد. این شرایط می تواند مانع از شکل گیری و تکامل حیات در سطح سیاره شود.",
            "کتاب تابستان به دلیل داستان جذاب و توصیف‌های زیبا از طبیعت و زندگی، توجه تمام علاقه‌مندان به ادبیات داستانی را به خود جلب می‌کند. این کتاب نه تنها احساسات عمیق انسانی را به تصویر می‌کشد بلکه خواننده را به دنیای خاطرات شیرین تابستان‌های کودکی می‌برد.",
            "حضرت ادریس علیه السلام به عنوان منشاء و معلم بسیاری از علوم شناخته می‌شود. او به عنوان یکی از قدیمی‌ترین پیشوایان علم، افکار بشر را به سمت استدلال و دقت در بحث سوق داده است. همچنین، او اولین کسی است که علم نجوم را به الهام الهی استخراج کرده و زمین را به چهار ربع تقسیم نموده است. در دعای روز اول ماه رجب نیز به علم ادریس اشاره شده است.",
            "ستاره‌های کوتوله سرخ معمولاً به صورت دوره‌ای شعله‌هایی از پرتوهای ماورا بنفش و اشعه X ساطع می‌کنند که می‌تواند اتمسفر سیارات اطراف را از بین ببرد و احتمال تشکیل حیات را کاهش دهد. اما ستاره Ross 128 به عنوان یک ستاره آرام شناخته می‌شود و این ویژگی باعث می‌شود که شرایط بهتری برای تشکیل حیات در سیاره Ross 128b فراهم شود.",
            "پوست کودکان به دلیل عدم تکامل کامل ملانوسیت‌ها، سیستم عروقی پوستی و توانایی تولید عرق حساس است. ملانوسیت‌ها که مسئول تولید ملانین هستند، از پوست در برابر اشعه ماورای بنفش محافظت می‌کنند. همچنین، سیستم عروقی پوستی در کودکان هنوز به طور کامل توسعه نیافته و این امر می‌تواند منجر به آسیب‌پذیری بیشتر پوست شود. علاوه بر این، پوست کودکان نمی‌تواند به اندازه کافی عرق تولید کند، که باعث می‌شود رطوبت پوست کاهش یابد. به همین دلیل، پوست کودکان به ویژه نوزادان به نسبت وزن بدن در معرض آسیب بیشتری قرار دارد.",
            "نزول این آیه به واکنش‌های معاصرین پیامبر اسلام، به ویژه ابوجهل و دیگر مخالفان، اشاره دارد که به دلیل عدم درک صحیح از معانی عمیق آیات و قدرت خداوند، به تمسخر و انکار آن می‌پرداختند. این آیه به نوعی به آنها پاسخ می‌دهد و نشان می‌دهد که حتی در آتش، درختی وجود دارد که فراتر از تصور آنهاست. این واکنش‌ها نشان‌دهنده چالش‌های اعتقادی و فکری در آن زمان بود.",
            "شرایط محیطی می‌تواند به عنوان فیلتر عمل کند زیرا عوامل متعددی مانند مقدار و نوع کالری، دما، اتمسفر، آب، خشکی، آفتاب، و بلایای طبیعی مانند آتشفشان و زلزله بر روی موجودات زنده تأثیر می‌گذارد. این عوامل می‌توانند موجودات را به چالش بکشند و تنها آن‌هایی که توانایی سازگاری با این شرایط را دارند، زنده می‌مانند و به نسل‌های بعدی منتقل می‌شوند.",
            "خشکی پوست ممکن است موقتی یا فصلی باشد. به عنوان مثال، در فصل زمستان به دلیل هوای سرد و خشک، بسیاری از افراد دچار خشکی پوست می‌شوند. در مقابل، در فصل‌های گرم و مرطوب، ممکن است این مشکل کاهش یابد. با این حال، برخی افراد ممکن است به طور دائمی با خشکی پوست مواجه باشند که نیاز به مراقبت و درمان مداوم دارد.",
            "سحابی خرچنگ دریایی، که با نام NGC 6357 شناخته می‌شود، به دلیل وجود ستاره‌های غیرمعمول روشن و عظیم در آن، به عنوان یک مکان مهم در کهکشان معرفی می‌شود. این سحابی همچنین خوشۀ ستاره‌ای باز Pismis 24 را در نزدیکی مرکز خود دارد که نشان‌دهنده فعالیت‌های شدید ستاره‌زایی در این ناحیه است. درخشش آبی در نزدیکی منطقه تشکیل ستاره داخلی ناشی از انتشار گاز هیدروژن یونیزه است که به جذابیت این سحابی افزوده است.",
            "سحابی خرچنگ ده سال نوری وسعت دارد و در مرکز آن یک تپ اختر قرار دارد. این تپ اختر به سنگینی خورشید اما به اندازه یک شهر کوچک است و ثانیه‌ای سی بار به دور خود می‌چرخد. همچنین، سحابی خرچنگ با سرعتی حدود 10000 کیلومتر بر ثانیه منبسط می‌شود و انتظار می‌رود که در چند هزار سال آینده به تدریج کم‌فروغ‌تر شده و سرانجام ناپدید گردد.",
            "وجود یک اقیانوس زیر سطحی در قمر اروپا می تواند شرایط لازم برای زندگی موجودات میکروسکوپی را فراهم کند. این اقیانوس می تواند شامل مواد مغذی و حرارت لازم برای حیات باشد. با توجه به اینکه بخار آب فوران شده از سطح اروپا ممکن است به این اقیانوس مرتبط باشد، بررسی های آینده می تواند به دانشمندان کمک کند تا پتانسیل اروپا برای تبدیل شدن به یک محل قابل سکونت را بدون نیاز به حفاری لایه یخ بررسی کنند.",
            "چگالش بوز-اینشتین حالتی از ماده است که در دماهای بسیار پایین ایجاد می‌شود و در آن اتم‌ها رفتار موجی خود را نشان می‌دهند. در این حالت، قوانین فیزیک کلاسیک به کنار می‌روند و فیزیک کوانتومی حاکم می‌شود. اتم‌ها در این حالت به گونه‌ای حرکت می‌کنند که انگار بر روی یکدیگر سوار هستند و این رفتار تنها در دماهای بسیار پایین قابل مشاهده است.",
            "در سال 2012، انجمن سلطنتی شیمی مسابقه‌ای را برای یافتن بهترین توضیح برای اثر امپمبا برگزار کرد. برنده این مسابقه نظریه‌ای را ارائه داد که علت این پدیده را 'ابرسرد شدن' می‌دانست. این نشان می‌دهد که این موضوع همچنان مورد توجه محققان و دانشمندان است و تلاش‌ها برای درک بهتر آن ادامه دارد.",
            "داستان کتاب عاشق آتشفشان در قرن هجدهم و در میان آشفتگی‌های دربار ناپلی اتفاق می‌افتد. این رمان به بررسی موضوعاتی چون عشق، تاریخ و روابط اجتماعی می‌پردازد و داستان زندگی سر ویلیام همیلتون و همسرش اِما را روایت می‌کند. همچنین، این داستان به تحولات سیاسی و اجتماعی آن زمان نیز اشاره دارد.",
            "انفجارهای هوایی به دلیل قدرت تخریب بالای خود و نادر بودن برخورد سیارک‌ها، خطرناک‌تر محسوب می‌شوند. در حالی که برخورد سیارک‌های بزرگ به ندرت اتفاق می‌افتد، انفجارهای هوایی می‌توانند به طور ناگهانی و بدون هشدار پیشین رخ دهند. به عنوان مثال، انفجار سیارکی به اندازه یک خانه در سال ۱۳۹۲ در چلیابینسک روسیه منجر به آسیب دیدن بیش از ۱۶۰۰ نفر شد. این نشان می‌دهد که انفجارهای هوایی می‌توانند تأثیرات جدی بر روی جمعیت‌های انسانی داشته باشند.",
            "پرتقال به دلیل خواص ضدعفونی‌کننده و ضد میکروبی که دارد، می‌تواند به درمان مشکلات پوستی کمک کند. به عنوان مثال، شما می‌توانید از پوست پرتقال له شده به عنوان مرهم برای اگزما و ناراحتی‌های پوستی استفاده کنید. این خاصیت به دلیل وجود ترکیبات طبیعی در پوست پرتقال است که به تسکین و بهبود وضعیت پوست کمک می‌کند.",
            "نوسانات درخشندگی ستاره KIC 8462852 به‌طور نامنظم و شدید اتفاق می‌افتند و این الگو با آنچه معمولاً در ستاره‌های دارای سیارات فراخورشیدی مشاهده می‌شود، متفاوت است. در حالی که وجود یک سیاره می‌تواند باعث نوسانات درخشندگی شود، در این مورد، نوسانات به‌قدری پیچیده و غیرقابل پیش‌بینی هستند که فرضیه‌های دیگر مانند وجود ابرهای میان ستاره‌ای، دنباله‌دارها یا حتی اَبَرسازه‌های بیگانگان فضایی نیز مطرح شده‌اند.",
            "پاریس به عنوان یک مقصد گردشگری محبوب به دلیل جاذبه‌های تاریخی، فرهنگی و هنری خود شناخته می‌شود. این شهر با برج ایفل، موزه لوور، کاتدرال نوتردام و خیابان‌های زیبا و پر از زندگی، هر ساله میلیون‌ها گردشگر را به خود جذب می‌کند. همچنین، فرهنگ غنی، غذاهای لذیذ و فضاهای رمانتیک پاریس، تجربه‌ای منحصر به فرد را برای بازدیدکنندگان فراهم می‌آورد. به همین دلیل، پاریس به عنوان 'شهر نور' و 'شهر عشق' در قلب بسیاری از مردم جهان جای دارد."
        ]
        
for text in texts:
    input_message = f"""{{"question": "{question}", "text": "{text}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 100
    }

    req = requests.post(url, headers=headers, json=payload)
    print(text)
    print(req.json()['choices'][0]['message']['content'])
    print("--------------------------------")

In [ ]:
from datasets import load_dataset

dataset = load_dataset("castorini/mr-tydi", "combined")

Generating train split: 100%|██████████| 48729/48729 [00:05<00:00, 9203.01 examples/s] 


In [16]:
id = 13000
print(f"query is : {dataset['train'][id]['query']}")

for data in dataset['train'][id]['positive_passages']:    
    print(f"passage positive is : {data['text']}")

for data in dataset['train'][id]['negative_passages']:    
    print(f"passage negative is : {data['text']}")

query is : দেবশ্রী রায়ের ডাক নাম কি ?
passage positive is : দেবশ্রী রায় এর জন্ম, বেড়ে ওঠা কলকাতায়। তার পিতার নাম বীরেন্দ্র কিশোর রায় এবং মায়ের নাম আরতি রায়। ১৯৬৯ সনে তিনি প্রথম "বালক গদাধর" নামে একটি চলচিত্রে শিশুশিল্পী হিসেবে অভিনয় করেন, যার পরিচালক ছিলেন হরিময় সেন। তিনি কলকাতার এ পি জে ,পার্ক স্ট্রীট শাখার স্কুলের ছাত্রী ছিলেন, যদিও নাচের প্রতি অত্যধিক ঝোঁক থাকার কারণে বেশিদূর এগোতে পারেন নি। তার ডাক নাম চুমকি।
passage negative is : নবী (সা.) এর মৃত্যুর পর জনগণ আবু বকর (রা.) খলিফা নির্বাচন করেন। তখন আয়িশা(রা.) নবী (সা.)এর স্ত্রী এবং খলিফার কন্যা হিসেবে সমধিক সম্মান পেতেন। এমনকি জনগণ তাকে নবীজি (সা.) এর কাছ থেকে "সিদ্দিক"(সত্যবাদী) উপাধি প্রাপ্ত আবু বকর (রা.) এর কন্যা হিসেবে "সিদ্দিকা বিনতু সিদ্দিক"(সত্যবাদীর কন্যা সত্যবাদিনী) বলে ডাকতে শুরু করে।[34] আবু বকর (রা.) তাঁর মৃত্যুর পূর্বকালে উমর (রা.) কে খলিফা নিযুক্ত করে যান।[34] খলিফা উমর (রা.)-এর শাসনামলেও তিনি দাপটের সাথে রাজনৈতিক সিদ্ধান্তসমূহে মতামত প্রদান করার স্বাধীনতা লাভ করেছিলেন।[34]
passage negative is : বঙ্গীয় কৃষক স

In [24]:
len(dataset['train'][id]['negative_passages'])

29

In [26]:
import requests
from dotenv import load_dotenv
import os
import time
from tqdm import tqdm

load_dotenv()

qwen = True
if qwen:
    url = "https://qwen3.chatllm.aiengines.ir/v1/chat/completions"
    model = "Qwen/Qwen3-4B-Instruct-2507"
    headers = {"Content-Type": "application/json", "Authorization": f"Bearer {os.getenv('LLM_AS_RERANKER_PASS')}"}
else:
    url = "http://192.168.130.206:4001/v1/chat/completions"
    model = "google/gemma-3-27b-it"
    headers = {"Content-Type": "application/json"}

instruction = """
You are a helpful assistant that help me to translate the text to persian language.
input text can be in any language.
your translation must be fluent and natural.
You must return just the translated text.
"""

id = 16010

query = dataset['train'][id]['query']
print(f"query is : {query}")
input_message = f"""{{"text": "{query}"}}"""
messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

payload = {
    "model": model,
    "messages": messages,
    "max_tokens": 1000
}

start_time = time.time()
req = requests.post(url, headers=headers, json=payload)
print(req.json()['choices'][0]['message']['content'])
print(f"time taken: {time.time() - start_time} seconds")
print("--------------------------------\n")


positive_passages = dataset['train'][id]['positive_passages']
for data in positive_passages:
    print(f"positive passages is : {data['text']}")
    input_message = f"""{{"text": "{data['text']}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 1000
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    print(req.json()['choices'][0]['message']['content'])
    print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

negative_passages = dataset['train'][id]['negative_passages']
for data in tqdm(negative_passages[:3]):
    print(f"negative passages is : {data['text']}")
    input_message = f"""{{"text": "{data['text']}"}}"""
    messages = [{"role": "system", "content": instruction}, {"role": "user", "content": input_message}]

    payload = {
        "model": model,
        "messages": messages,
        "max_tokens": 1000
    }
    start_time = time.time()
    req = requests.post(url, headers=headers, json=payload)
    print(req.json()['choices'][0]['message']['content'])
    print(f"time taken: {time.time() - start_time} seconds")
    print("--------------------------------\n")

query is : Is Death in the Discworld series?
در سریهای دیسک ورلد، مرگ وجود دارد؟
time taken: 0.4940967559814453 seconds
--------------------------------

positive passages is : Death is a fictional character in Terry Pratchett's Discworld series and a parody of several other personifications of death. Like most Grim Reapers, he is a black-robed skeleton usually carrying a scythe. His jurisdiction is specifically the Discworld itself; he is only a part, or minion, of Azrael, the universal Death. He has been generally used by Pratchett to explore the problems of human existence, and has become more sympathetic throughout the series.
میلیون‌ها سال پیش، در سری سری دیسک ورلد تری تراچیت، دهیم یک شخصیت تخیلی است که از نظر بسیاری از شخصیت‌های دیگر می‌باشد. مانند بیشتر ریپرها، یک اسکلت با رُب سیاه است که معمولاً یک کمان دارد. حوزه کار او به ویژه دیسک ورلد است؛ او تنها یک بخش یا مینیون از آذرال، مرگ جهانی است. او به طور کلی توسط تری تراچیت برای بررسی مسائل وجود انسان استفاده شده و در طول سری به 

  0%|          | 0/3 [00:00<?, ?it/s]

negative passages is : Kirby’s most significant move of the 80s was teaming up with Pratchett, a commission that Kirby thought would be a "one-off". He was eventually commissioned to produce the covers for the "Discworld" series, producing 26 covers before his death in 2001. Beginning with the twenty-seventh "Discworld" novel, "The Last Hero" (2001), Paul Kidby took over as cover illustrator.


 33%|███▎      | 1/3 [00:02<00:04,  2.06s/it]

رویداد مهم‌تر این دهه برای کیری، همکاری با پراچتت بود که این کار را کیری به عنوان یک "مهمت یکباره" در نظر می‌گرفت. در نهایت، او در تولید پوشش‌های سری «دیسک ورلد» به عنوان یک میانه تولید شد و 26 پوشش در سال 2001 که سال فوتیاش بود، تولید کرد. از نسخه 27 مجموعه «دیسک ورلد» به نام «آخرین سرای» (2001)، پال کیدبی به عنوان موسیقی سری پوشش‌ها جایگزین شد.
time taken: 2.056161880493164 seconds
--------------------------------

negative passages is : The majority of Discworld Witches are seen in the Ramtops region of Discworld, and, barring the latest book in the Tiffany Aching series, the primary protagonists of the Witch books are from Lancre, a country in the Ramtops region.


 67%|██████▋   | 2/3 [00:03<00:01,  1.64s/it]

بیشترین تعداد مغزهای دیسک وورلд در منطقه رامتوپس از دیسک وورلد مشاهده می‌شود و متن اصلی کتاب‌های مغزهای دیسک وورلد، ممکن است به جز کتاب آخر سری تیفانی اچینگ، از کشور لانکر، که در منطقه رامتوپس قرار دارد، بیان می‌شود.
time taken: 1.348144292831421 seconds
--------------------------------

negative passages is : The Wit and Wisdom of Discworld is an accessory book to the Discworld series by Terry Pratchett. It is a compilation of quotes from all the Discworld novels, amassed and prefaced by Stephen Briggs.


100%|██████████| 3/3 [00:04<00:00,  1.52s/it]

"ذکر و حکمت دیسک ورلд" کتابی میانه است که به سری دیسک ورلد از تری پراچت مربوط است. این کتاب شامل عباراتی از تمام کتاب‌های دیسک ورلد است که توسط استیفان بریگس جمع‌آوری و با مقدمه‌ای نوشته شده است.
time taken: 1.163712739944458 seconds
--------------------------------

